In [1]:
import pandas as pd
import os
from pathlib import Path
import pathlib
from collections import defaultdict
import nltk
from nltk.corpus import stopwords
import json

In [2]:
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package punkt to /home/kane_wu/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/kane_wu/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [3]:
import string
def clean(data):
    # change all to lowercase
    data['text'] = data['text'].apply(str.lower)

    # tokenize
    data['tokens'] = data['text'].apply(nltk.word_tokenize)
    
    # remove punctuation
    data['tokens'] = data['tokens'].apply(lambda tokens: [token.translate(str.maketrans('', '', string.punctuation)) for token in tokens])
    
    # remove tokens that are not alphabetic
    data['tokens'] = data['tokens'].apply(lambda tokens: [token for token in tokens if token.isalpha()])
    
    # remove stop words
    stop_words = set(stopwords.words('english'))
    data['tokens'] = data['tokens'].apply(lambda tokens: [token for token in tokens if token not in stop_words])
    
    # pos tag
    data['pos_tag'] = data['tokens'].apply(nltk.pos_tag)
    
    return data

In [4]:
DATA_PATH = pathlib.Path().resolve().parent.joinpath(Path(r"POS Tagging/data/reviewSelected100.json"))
if os.path.exists('./cleaned_data.json'):
    with open('./cleaned_data.json') as f:
        data = json.load(f)
else:
    data = pd.read_json(DATA_PATH, lines=True,encoding = "ISO-8859-1")
    data.drop(['review_id', 'user_id'], inplace=True, axis=1)
    data = clean(data)

In [5]:
data.head()

business_id  stars  useful  funny  cool  \
0  ZBE-H_aUlicix_9vUGQPIQ      5       0      0     0   
1  e-YnECeZNt8ngm0tu4X9mQ      4       0      0     0   
2  j7HO1YeMQGYo3KibMXZ5vg      5       2      1     3   
3  7e3PZzUpG5FYOTGt3O3ePA      3       0      0     0   
4  vuHzLZ7nAeT-EiecOkS5Og      1      11      0     3   

                                                text                date  \
0  we had my mother's birthday party here on 10/2... 2016-11-09 20:07:25   
1  good korean grill near eaton centre. the marin... 2015-12-05 05:06:43   
2  was recommended to try this place by few peopl... 2014-10-11 05:16:15   
3  ambience: would not expect something this nice... 2016-07-25 03:45:26   
4  absolutely the worst pool company that i have ... 2016-04-11 18:49:11   

                                              tokens  \
0  [mother, birthday, party, great, time, food, m...   
1  [good, korean, grill, near, eaton, centre, mar...   
2  [recommended, try, place, people, today, first...   
3  [ambience, would, expect, something, nice, can...   
4  [absolutely, worst, pool, company, ever, deal,...   

                                             pos_tag  
0  [(mother, NN), (birthday, NN), (party, NN), (g...  
1  [(good, JJ), (korean, NN), (grill, NN), (near,...  
2  [(recommended, VBN), (try, JJ), (place, NN), (...  
3  [(ambience, NN), (would, MD), (expect, VB), (s...  
4  [(absolutely, RB), (worst, JJS), (pool, NN), (...

In [6]:
NOUN_TAGS = set(['NN', 'NNS', 'NNP', 'NNPS'])


In [7]:
def count_noun(reviews):
    for word, tag in reviews:
         if tag in NOUN_TAGS:
            counts[word] += 1

In [8]:
businesses = defaultdict(defaultdict)
business_groups = data.groupby('business_id')
# some sentiment analysis
from nltk.sentiment.vader import SentimentIntensityAnalyzer
import copy
nltk.download('vader_lexicon')
def sentiment_analysis(sentence):
     # compound
     # -1 to -.51 very bad
     # -.50 to -.1 bad
     # 0 neutral
     # .1 to .5 good
     # .51 to 1 very good
     sid = SentimentIntensityAnalyzer()
     ss = sid.polarity_scores(sentence)
     for k in sorted(ss):
         print(f"{k}: {ss[k]} \n")
      
     if -1 <= ss['compound'] <= -.51:
         sentiments['very_bad'] += 1
     elif -.5 <= ss['compound'] <= -.1:
         sentiments['bad'] += 1
     elif ss['compound'] == 0:
         sentiments['neutral'] += 1
     elif .1 <= ss['compound'] <= .5:
         sentiments['good'] += 1
     elif .51 <= ss['compound'] <= 1:
         sentiments['very_good'] += 1
    
for business in business_groups.indices:
    counts = defaultdict(int)
    sentiments = defaultdict(int)
    business_df = business_groups.get_group(business)
    business_df['pos_tag'].apply(count_noun)
    business_df['text'].apply(sentiment_analysis)

    counts = [(word, count) for word, count in counts.items()]
    counts.sort(key = lambda x: x[1], reverse=True)
    
    businesses[business]['nouns'] = copy.deepcopy(counts)
    businesses[business]['sentiment'] = copy.deepcopy(sentiments)  
    

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /home/kane_wu/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


compound: 0.8534 

neg: 0.03 

neu: 0.811 

pos: 0.16 

compound: 0.9661 

neg: 0.0 

neu: 0.656 

pos: 0.344 

compound: 0.9477 

neg: 0.0 

neu: 0.598 

pos: 0.402 

compound: 0.8625 

neg: 0.0 

neu: 0.675 

pos: 0.325 

compound: 0.9359 

neg: 0.0 

neu: 0.627 

pos: 0.373 

compound: 0.9075 

neg: 0.0 

neu: 0.514 

pos: 0.486 

compound: 0.9703 

neg: 0.021 

neu: 0.805 

pos: 0.174 

compound: 0.8791 

neg: 0.042 

neu: 0.801 

pos: 0.158 

compound: 0.9425 

neg: 0.049 

neu: 0.582 

pos: 0.369 

compound: 0.8363 

neg: 0.089 

neu: 0.758 

pos: 0.153 

compound: 0.9476 

neg: 0.0 

neu: 0.91 

pos: 0.09 

compound: 0.7666 

neg: 0.141 

neu: 0.633 

pos: 0.226 

compound: -0.7963 

neg: 0.151 

neu: 0.766 

pos: 0.082 

compound: 0.9879 

neg: 0.057 

neu: 0.701 

pos: 0.241 

compound: -0.6684 

neg: 0.083 

neu: 0.856 

pos: 0.061 

compound: 0.0129 

neg: 0.0 

neu: 0.972 

pos: 0.028 

compound: 0.7564 

neg: 0.119 

neu: 0.63 

pos: 0.251 

compound: 0.9534 

neg: 0.045 


compound: 0.9568 

neg: 0.0 

neu: 0.807 

pos: 0.193 

compound: 0.5266 

neg: 0.075 

neu: 0.749 

pos: 0.176 

compound: 0.9768 

neg: 0.0 

neu: 0.706 

pos: 0.294 

compound: 0.7893 

neg: 0.043 

neu: 0.732 

pos: 0.225 

compound: 0.9945 

neg: 0.019 

neu: 0.752 

pos: 0.229 

compound: 0.6801 

neg: 0.031 

neu: 0.875 

pos: 0.094 

compound: -0.8145 

neg: 0.233 

neu: 0.638 

pos: 0.13 

compound: -0.1134 

neg: 0.056 

neu: 0.897 

pos: 0.047 

compound: 0.788 

neg: 0.039 

neu: 0.874 

pos: 0.086 

compound: 0.9879 

neg: 0.0 

neu: 0.698 

pos: 0.302 

compound: 0.9688 

neg: 0.046 

neu: 0.739 

pos: 0.215 

compound: 0.8371 

neg: 0.028 

neu: 0.877 

pos: 0.095 

compound: 0.9858 

neg: 0.029 

neu: 0.753 

pos: 0.218 

compound: 0.9872 

neg: 0.021 

neu: 0.786 

pos: 0.193 

compound: 0.9803 

neg: 0.035 

neu: 0.85 

pos: 0.115 

compound: 0.9329 

neg: 0.074 

neu: 0.817 

pos: 0.109 

compound: 0.9348 

neg: 0.0 

neu: 0.69 

pos: 0.31 

compound: 0.9814 

neg: 0

compound: -0.717 

neg: 0.221 

neu: 0.704 

pos: 0.075 

compound: 0.8674 

neg: 0.0 

neu: 0.791 

pos: 0.209 

compound: 0.0772 

neg: 0.036 

neu: 0.923 

pos: 0.041 

compound: 0.3506 

neg: 0.0 

neu: 0.841 

pos: 0.159 

compound: -0.0971 

neg: 0.116 

neu: 0.758 

pos: 0.126 

compound: -0.7854 

neg: 0.099 

neu: 0.882 

pos: 0.019 

compound: 0.8151 

neg: 0.039 

neu: 0.863 

pos: 0.099 

compound: 0.4667 

neg: 0.0 

neu: 0.776 

pos: 0.224 

compound: 0.0258 

neg: 0.042 

neu: 0.914 

pos: 0.044 

compound: -0.7401 

neg: 0.157 

neu: 0.843 

pos: 0.0 

compound: -0.9505 

neg: 0.12 

neu: 0.849 

pos: 0.031 

compound: 0.8965 

neg: 0.0 

neu: 0.603 

pos: 0.397 

compound: 0.9698 

neg: 0.091 

neu: 0.657 

pos: 0.252 

compound: -0.9478 

neg: 0.179 

neu: 0.755 

pos: 0.065 

compound: -0.9358 

neg: 0.26 

neu: 0.718 

pos: 0.022 

compound: 0.9321 

neg: 0.0 

neu: 0.755 

pos: 0.245 

compound: 0.9876 

neg: 0.015 

neu: 0.892 

pos: 0.093 

compound: -0.4877 

ne

compound: 0.8977 

neg: 0.0 

neu: 0.63 

pos: 0.37 

compound: 0.9576 

neg: 0.069 

neu: 0.547 

pos: 0.384 

compound: 0.9133 

neg: 0.0 

neu: 0.545 

pos: 0.455 

compound: 0.9951 

neg: 0.026 

neu: 0.729 

pos: 0.244 

compound: 0.9681 

neg: 0.0 

neu: 0.621 

pos: 0.379 

compound: -0.9442 

neg: 0.111 

neu: 0.827 

pos: 0.061 

compound: 0.8717 

neg: 0.038 

neu: 0.683 

pos: 0.279 

compound: 0.9637 

neg: 0.0 

neu: 0.806 

pos: 0.194 

compound: 0.9895 

neg: 0.027 

neu: 0.84 

pos: 0.133 

compound: 0.6178 

neg: 0.132 

neu: 0.689 

pos: 0.179 

compound: 0.9403 

neg: 0.039 

neu: 0.81 

pos: 0.15 

compound: 0.9943 

neg: 0.023 

neu: 0.784 

pos: 0.194 

compound: 0.9433 

neg: 0.0 

neu: 0.878 

pos: 0.122 

compound: 0.938 

neg: 0.059 

neu: 0.716 

pos: 0.225 

compound: -0.8665 

neg: 0.097 

neu: 0.857 

pos: 0.046 

compound: 0.9996 

neg: 0.024 

neu: 0.767 

pos: 0.209 

compound: 0.9262 

neg: 0.0 

neu: 0.732 

pos: 0.268 

compound: 0.9902 

neg: 0.0 



...

compound: 0.9846 

neg: 0.036 

neu: 0.801 

pos: 0.163 

compound: 0.9955 

neg: 0.021 

neu: 0.717 

pos: 0.262 

compound: 0.9896 

neg: 0.074 

neu: 0.778 

pos: 0.147 

compound: -0.7264 

neg: 0.134 

neu: 0.789 

pos: 0.077 

compound: 0.9873 

neg: 0.018 

neu: 0.797 

pos: 0.185 

compound: -0.1027 

neg: 0.036 

neu: 0.964 

pos: 0.0 

compound: 0.1888 

neg: 0.065 

neu: 0.852 

pos: 0.083 

compound: -0.7059 

neg: 0.113 

neu: 0.842 

pos: 0.045 

compound: 0.8901 

neg: 0.067 

neu: 0.784 

pos: 0.149 

compound: 0.4951 

neg: 0.1 

neu: 0.78 

pos: 0.12 

compound: 0.9547 

neg: 0.0 

neu: 0.796 

pos: 0.204 

compound: 0.9888 

neg: 0.004 

neu: 0.886 

pos: 0.109 

compound: 0.9966 

neg: 0.006 

neu: 0.756 

pos: 0.239 

compound: 0.6998 

neg: 0.053 

neu: 0.656 

pos: 0.291 

compound: 0.9977 

neg: 0.069 

neu: 0.753 

pos: 0.178 

compound: 0.9515 

neg: 0.0 

neu: 0.813 

pos: 0.187 

compound: -0.8619 

neg: 0.143 

neu: 0.769 

pos: 0.088 

compound: 0.9884 

n

compound: 0.9783 

neg: 0.0 

neu: 0.709 

pos: 0.291 

compound: 0.6952 

neg: 0.0 

neu: 0.855 

pos: 0.145 

compound: 0.8213 

neg: 0.0 

neu: 0.916 

pos: 0.084 

compound: 0.9618 

neg: 0.0 

neu: 0.733 

pos: 0.267 

compound: 0.9618 

neg: 0.0 

neu: 0.831 

pos: 0.169 

compound: 0.8764 

neg: 0.072 

neu: 0.592 

pos: 0.336 

compound: 0.9738 

neg: 0.0 

neu: 0.845 

pos: 0.155 

compound: 0.9886 

neg: 0.009 

neu: 0.813 

pos: 0.178 

compound: 0.6369 

neg: 0.0 

neu: 0.724 

pos: 0.276 

compound: -0.5673 

neg: 0.03 

neu: 0.959 

pos: 0.011 

compound: 0.7909 

neg: 0.014 

neu: 0.91 

pos: 0.075 

compound: 0.9578 

neg: 0.021 

neu: 0.878 

pos: 0.102 

compound: 0.6876 

neg: 0.037 

neu: 0.888 

pos: 0.075 

compound: 0.9547 

neg: 0.0 

neu: 0.851 

pos: 0.149 

compound: 0.9461 

neg: 0.0 

neu: 0.77 

pos: 0.23 

compound: 0.8695 

neg: 0.062 

neu: 0.786 

pos: 0.153 

compound: 0.9405 

neg: 0.0 

neu: 0.749 

pos: 0.251 

compound: 0.5719 

neg: 0.0 

neu: 0.

compound: -0.8851 

neg: 0.13 

neu: 0.87 

pos: 0.0 

compound: -0.984 

neg: 0.173 

neu: 0.75 

pos: 0.077 

compound: 0.69 

neg: 0.01 

neu: 0.928 

pos: 0.062 

compound: -0.2357 

neg: 0.102 

neu: 0.816 

pos: 0.083 

compound: -0.9358 

neg: 0.191 

neu: 0.745 

pos: 0.065 

compound: -0.5849 

neg: 0.081 

neu: 0.919 

pos: 0.0 

compound: 0.9517 

neg: 0.0 

neu: 0.638 

pos: 0.362 

compound: 0.9907 

neg: 0.041 

neu: 0.761 

pos: 0.198 

compound: -0.9754 

neg: 0.131 

neu: 0.811 

pos: 0.058 

compound: 0.9763 

neg: 0.0 

neu: 0.884 

pos: 0.116 

compound: 0.9627 

neg: 0.0 

neu: 0.736 

pos: 0.264 

compound: 0.9451 

neg: 0.0 

neu: 0.765 

pos: 0.235 

compound: -0.7243 

neg: 0.082 

neu: 0.858 

pos: 0.06 

compound: 0.9081 

neg: 0.088 

neu: 0.566 

pos: 0.346 

compound: -0.9812 

neg: 0.164 

neu: 0.836 

pos: 0.0 

compound: 0.338 

neg: 0.093 

neu: 0.81 

pos: 0.097 

compound: 0.9517 

neg: 0.025 

neu: 0.747 

pos: 0.229 

compound: -0.9722 

neg: 0.104

compound: 0.9349 

neg: 0.063 

neu: 0.488 

pos: 0.448 

compound: 0.953 

neg: 0.0 

neu: 0.598 

pos: 0.402 

compound: 0.9476 

neg: 0.0 

neu: 0.697 

pos: 0.303 

compound: -0.8346 

neg: 0.152 

neu: 0.848 

pos: 0.0 

compound: 0.8513 

neg: 0.036 

neu: 0.772 

pos: 0.192 

compound: 0.9413 

neg: 0.0 

neu: 0.587 

pos: 0.413 

compound: 0.8341 

neg: 0.041 

neu: 0.77 

pos: 0.189 

compound: 0.9112 

neg: 0.095 

neu: 0.461 

pos: 0.443 

compound: 0.8825 

neg: 0.062 

neu: 0.669 

pos: 0.269 

compound: -0.7367 

neg: 0.204 

neu: 0.618 

pos: 0.179 

compound: 0.3063 

neg: 0.12 

neu: 0.716 

pos: 0.164 

compound: 0.9456 

neg: 0.0 

neu: 0.754 

pos: 0.246 

compound: 0.9018 

neg: 0.0 

neu: 0.716 

pos: 0.284 

compound: 0.9645 

neg: 0.071 

neu: 0.719 

pos: 0.21 

compound: -0.5574 

neg: 0.084 

neu: 0.865 

pos: 0.052 

compound: 0.2675 

neg: 0.097 

neu: 0.8 

pos: 0.103 

compound: 0.9856 

neg: 0.0 

neu: 0.571 

pos: 0.429 

compound: 0.5905 

neg: 0.0 

n

compound: 0.8791 

neg: 0.0 

neu: 0.913 

pos: 0.087 

compound: 0.8518 

neg: 0.028 

neu: 0.868 

pos: 0.104 

compound: 0.54 

neg: 0.0 

neu: 0.83 

pos: 0.17 

compound: 0.8625 

neg: 0.0 

neu: 0.809 

pos: 0.191 

compound: 0.9752 

neg: 0.026 

neu: 0.845 

pos: 0.129 

compound: 0.8248 

neg: 0.035 

neu: 0.863 

pos: 0.102 

compound: 0.8344 

neg: 0.138 

neu: 0.387 

pos: 0.476 

compound: 0.0685 

neg: 0.088 

neu: 0.848 

pos: 0.064 

compound: 0.9642 

neg: 0.0 

neu: 0.635 

pos: 0.365 

compound: 0.9115 

neg: 0.06 

neu: 0.722 

pos: 0.218 

compound: 0.976 

neg: 0.0 

neu: 0.718 

pos: 0.282 

compound: 0.9719 

neg: 0.0 

neu: 0.812 

pos: 0.188 

compound: 0.9357 

neg: 0.052 

neu: 0.754 

pos: 0.195 

compound: 0.8519 

neg: 0.08 

neu: 0.713 

pos: 0.207 

compound: 0.8955 

neg: 0.0 

neu: 0.638 

pos: 0.362 

compound: 0.9892 

neg: 0.056 

neu: 0.733 

pos: 0.21 

compound: 0.9786 

neg: 0.025 

neu: 0.812 

pos: 0.163 

compound: 0.9536 

neg: 0.0 

neu: 0

In [9]:
for business, attributes in businesses.items():
    nouns = attributes['nouns']
    print(f"Top 10 nouns in {business}\n")
    for idx, (noun, count) in enumerate(nouns):
        print(f"{noun} | {count}")
        if idx == 10:
            break
    sentiments = attributes['sentiment']
    print(f"sentiments:\n")

    for sentiment, count in sentiments.items():
        print(f"{sentiment} | {count}")
    print(f"\n\n\n")

Top 10 nouns in --I7YYLada0tSLkORTHb5Q

food | 72
place | 59
service | 52
wings | 38
bar | 31
time | 30
beer | 27
fries | 26
nt | 18
chicken | 18
night | 16
sentiments:

very_good | 82
very_bad | 8
good | 4
bad | 3
neutral | 1




Top 10 nouns in -7XWJYkutqhIxLen7Grg1g

sushi | 122
food | 91
service | 75
place | 75
order | 48
ayce | 37
rolls | 35
time | 35
prince | 35
eat | 33
places | 33
sentiments:

very_good | 82
bad | 5
good | 5
very_bad | 8




Top 10 nouns in 0Rni7ocMC_Lg2UH0lDeKMQ

pizza | 120
order | 51
wings | 46
time | 37
place | 37
minutes | 29
food | 27
service | 24
kids | 17
crust | 17
barro | 16
sentiments:

very_good | 67
very_bad | 17
good | 10
bad | 5




Top 10 nouns in 0kPm1zEpeXFRg8D2phqgCQ

coffee | 95
donuts | 64
order | 50
service | 42
time | 41
location | 34
dunkin | 24
minutes | 22
place | 21
customer | 20
manager | 20
sentiments:

very_good | 40
very_bad | 31
good | 14
bad | 10




Top 10 nouns in 1Fpk8ibHhZYnCw8fnGny8w

food | 100
service | 53
place | 51
rice

bad | 6
good | 7




Top 10 nouns in NdpvGGF4cLrdnA6ydSZz3g

food | 132
service | 114
pot | 93
place | 77
soup | 59
time | 49
order | 44
base | 40
cream | 37
quality | 36
price | 35
sentiments:

bad | 6
very_good | 71
very_bad | 15
neutral | 1
good | 6




Top 10 nouns in NnxwkiBvSSyKeFiez0DDcQ

store | 80
service | 52
barney | 46
barneys | 45
vegas | 38
selection | 36
sales | 33
staff | 31
time | 30
customer | 29
shoes | 27
sentiments:

very_good | 88
very_bad | 6
good | 5




Top 10 nouns in OjnRf8yDGEBCoUDdchSViw

food | 155
truck | 107
jamburrito | 45
cajun | 39
time | 36
puppies | 36
burrito | 36
jamburritos | 34
sauce | 30
jambalaya | 29
hush | 25
sentiments:

good | 6
very_good | 88
very_bad | 4
bad | 1
neutral | 1




Top 10 nouns in PyMcV7WSYVqg1_S29G109g

car | 235
wash | 140
place | 55
service | 54
time | 48
oil | 37
job | 34
vehicle | 27
nt | 24
guy | 24
change | 23
sentiments:

neutral | 2
bad | 12
very_bad | 32
very_good | 35
good | 13




Top 10 nouns in QaFO4S6HFUu2NIbe

time | 35
location | 33
years | 23
guys | 22
today | 22
sentiments:

good | 6
very_good | 68
very_bad | 16
bad | 5
neutral | 3




Top 10 nouns in c1_adyjYG6JEa1PZAXMOBg

food | 125
service | 59
place | 51
dosa | 51
chicken | 48
butter | 32
spicy | 31
buffet | 30
restaurant | 29
time | 28
mutton | 26
sentiments:

very_good | 79
good | 7
bad | 4
neutral | 2
very_bad | 7




Top 10 nouns in cOY6ipigtTXdcmmmiFiniA

food | 115
place | 91
breakfast | 80
service | 62
coffee | 62
time | 50
order | 32
minutes | 29
waitress | 28
side | 24
eggs | 22
sentiments:

very_good | 85
good | 2
very_bad | 6
bad | 4
neutral | 1




Top 10 nouns in cPzIic1AqH1ApTVVaww5hw

sushi | 76
service | 65
place | 64
food | 60
roll | 50
ayce | 39
rolls | 39
quality | 35
menu | 34
time | 34
price | 32
sentiments:

very_good | 60
very_bad | 16
bad | 11
neutral | 3
good | 9




Top 10 nouns in caq9CTtWB-8K0tdFUhTfAQ

food | 112
pasta | 75
service | 56
place | 45
location | 41
pizza | 38
sauce | 37
nt | 34
grazie | 30
or

order | 29
menu | 27
sentiments:

very_good | 90
very_bad | 1
bad | 3
good | 2
neutral | 3




Top 10 nouns in yAkaDc6MWX3dy8bnEcCrRQ

food | 137
place | 65
service | 47
chicken | 44
madison | 38
time | 37
restaurant | 37
order | 31
dishes | 29
years | 27
garden | 27
sentiments:

very_bad | 10
neutral | 3
good | 7
very_good | 73
bad | 6




Top 10 nouns in yEZn1XpLsEC9uBa-X4xAZw

mi | 77
banh | 61
sandwiches | 55
place | 54
food | 42
sandwich | 39
service | 25
tea | 24
vua | 21
pork | 19
options | 17
sentiments:

very_good | 84
neutral | 5
very_bad | 5
good | 2
bad | 2




Top 10 nouns in yHHVKa9joZAKiBDUp2SkKw

coffee | 82
place | 64
food | 51
vegan | 28
time | 26
sandwich | 26
menu | 25
sandwiches | 24
staff | 21
service | 20
nt | 20
sentiments:

very_good | 89
good | 3
bad | 4
very_bad | 4




Top 10 nouns in z8Em-bhZI3Mmspml7tj6tg

bbq | 96
food | 73
place | 66
brisket | 55
pork | 41
meat | 32
sauce | 31
barbecue | 29
order | 27
nt | 26
beans | 25
sentiments:

very_good | 58
good |

In [10]:
yelp_biz = pd.read_json('yelp_academic_dataset_business.json',lines=True,encoding = "ISO-8859-1")

In [11]:
yelp_biz.describe()

latitude      longitude          stars   review_count  \
count  160585.000000  160585.000000  160585.000000  160585.000000   
mean       38.759794     -94.266212       3.656954      51.964548   
std         7.138042      19.975446       0.943604     130.030448   
min        27.998972    -123.393929       1.000000       5.000000   
25%        30.355886    -122.589583       3.000000       8.000000   
50%        42.177366     -84.383281       4.000000      17.000000   
75%        45.458531     -81.288501       4.500000      44.000000   
max        49.490000      71.113271       5.000000    9185.000000   

             is_open  
count  160585.000000  
mean        0.767494  
std         0.422431  
min         0.000000  
25%         1.000000  
50%         1.000000  
75%         1.000000  
max         1.000000

In [12]:
yelp_biz_dict = { row['business_id']: row for _, row in yelp_biz.iterrows() }

In [13]:
list(businesses.values())

[defaultdict(None,
             {'nouns': [('food', 72),
               ('place', 59),
               ('service', 52),
               ('wings', 38),
               ('bar', 31),
               ('time', 30),
               ('beer', 27),
               ('fries', 26),
               ('nt', 18),
               ('chicken', 18),
               ('night', 16),
               ('sports', 15),
               ('burger', 15),
               ('selection', 14),
               ('server', 14),
               ('beers', 13),
               ('drinks', 13),
               ('times', 12),
               ('burgers', 12),
               ('husband', 11),
               ('order', 11),
               ('staff', 11),
               ('moose', 9),
               ('sliders', 9),
               ('waitress', 9),
               ('restaurant', 9),
               ('sandwich', 9),
               ('everything', 8),
               ('quality', 8),
               ('bill', 8),
               ('salad', 8),
               ('way', 8

In [14]:
businesses_good_to_bad = list(businesses.values())
businesses_good_to_bad.sort(key=lambda x: x['sentiment']['very_good'] * 5 \
                                       + x['sentiment']['good'] * 1 \
                                       - x['sentiment']['bad'] * 1 \
                                       - x['sentiment']['very_bad'] * 5, reverse=True)
print(businesses_good_to_bad[0]['sentiment'])

defaultdict(<class 'int'>, {'very_good': 98, 'very_bad': 1, 'good': 0, 'bad': 0})


In [ ]:
count = 0
# businesses.keys()
# yelp_biz_dict.keys()
for business_id in businesses.keys():
    print(business_id)
    if business_id in yelp_biz_dict.keys():
        print(yelp_biz_dict[business_id]['name'])
        count += 1
        
print(f"{count} out of {len(businesses)} have corresponding names\n")

print(yelp_biz_dict.keys())

In [ ]:
!jupyter notebook --NotebookApp.iopub_data_rate_limit=1.0e10

[I 22:51:24.696 NotebookApp] The port 8888 is already in use, trying another port.
[I 22:51:24.697 NotebookApp] Serving notebooks from local directory: /home/kane_wu/CZ4045/Application
[I 22:51:24.697 NotebookApp] Jupyter Notebook 6.4.4 is running at:
[I 22:51:24.697 NotebookApp] http://localhost:8889/?token=d8a4e02bf663caee0f0f63141da9ed310262814d538112e1
[I 22:51:24.697 NotebookApp]  or http://127.0.0.1:8889/?token=d8a4e02bf663caee0f0f63141da9ed310262814d538112e1
[I 22:51:24.697 NotebookApp] Use Control-C to stop this server and shut down all kernels (twice to skip confirmation).
[C 22:51:25.085 NotebookApp] 
    
    To access the notebook, open this file in a browser:
        file:///home/kane_wu/.local/share/jupyter/runtime/nbserver-2756-open.html
    Or copy and paste one of these URLs:
        http://localhost:8889/?token=d8a4e02bf663caee0f0f63141da9ed310262814d538112e1
     or http://127.0.0.1:8889/?token=d8a4e02bf663caee0f0f63141da9ed310262814d538112e1


In [16]:
import pickle
with open('businesses.pickle', "wb") as f:
    pickle.dump(businesses, f)
    
with open('yelp_businesses.pickle', "wb") as f:
    pickle.dump(yelp_biz_dict, f)